# Importa bibliotecas

In [0]:
# import pyspark
from pyspark.sql import SparkSession
from pyspark.sql.functions import col
import os

# Cria uma SparkSession

In [0]:
# spark = SparkSession.builder.master('local[*]').getOrCreate()

# Importa dados

In [0]:
BASE_PATH = '/Volumes/fiap_postech_covid19_pnad'

INPUT_PATH = f'{BASE_PATH}/ingest/ingest_raw/micro_data'
# BRONZE_PATH = f'{BASE_PATH}/bronze/bronze_raw'
SILVER_PATH = f'{BASE_PATH}/silver/silver_volume'
GOLD_PATH = f'{BASE_PATH}/gold/gold_volume'

path_covid_drive = '/content/drive/MyDrive/Pós Tech/Tech Challenges/Tech Challenge 3/data/silver'
df_covid = spark.read.parquet(SILVER_PATH, header=True)

In [0]:
path_dicionarios = f'{SILVER_PATH}/dicionario_valores_pnad_covid.csv'
df_dicionario_valores = spark.read.csv(path_dicionarios, header=True, inferSchema=False)

# Junta a base Covid19 com o dicionário de códigos

In [0]:
df_covid_com_valores = df_covid

for column in df_covid.columns[1:]:
    # Cria dicionário de códigos/valores
    df_filtro = df_dicionario_valores.where(df_dicionario_valores['CODIGO'] == column)
    dict_from_df_filtro = df_filtro.select('SUB_CODIGO', 'DESCRICAO').rdd.collectAsMap()

    # Converte chaves para string
    dict_from_df_filtro = {str(k): str(v) for k, v in dict_from_df_filtro.items()}
    df_covid_com_valores = df_covid_com_valores.withColumn(column, col(column).cast('string'))

    # Substitui códigos da base pelos valores do dicionário
    df_covid_com_valores = df_covid_com_valores.replace(to_replace=dict_from_df_filtro, subset=[column])

# Seleciona colunas necessárias

In [0]:
df_covid_com_valores.createOrReplaceTempView('df_covid_com_valores')

In [0]:
covid_tratado = spark.sql(
    '''
    SELECT
      A002 as idade,
      A003 as sexo,
      A004 as cor_raca,
      B0011 as febre,
      A005 as escolaridade,
      B00111 as perda_cheiro_sabor,
      B0012 as tosse,
      B0014 as dificuldade_respirar,
      B002 as foi_hospital,
      B009A as fez_swab,
      B011 as resultado_teste,
      B0019 as fadiga,
      B007 as plano_de_saude,
      B008 as fez_teste_covid,
      B009C as coleta_sangue_furo_dedo,
      B009E as coleta_sangue_veia,
      C007A as area_trabalho,
      C011A as remuneracao,
      C013 as trabalho_remoto,
      D0031 as bolsa_familia,
      A006 as frequenta_escola,
      B00112 as dor_muscular,
      B00113 as diarreia,
      B0016 as dor_peito,
      B0031 as ficou_em_casa,
      B0033 as tomou_remedio_conta_propria,
      B0035 as recebeu_visita_sus,
      B0042 as buscou_pronto_socorro_sus_upa,
      B005 as ficou_internado,
      B006 as foi_sedado,
      B0103 as tem_asma_bronquite,
      C007C as cargo_no_trabalho,
      C007E as qtd_empregados_no_trabalho,
      C010 as remuneracao_em_todos_trabalhos,
      C012 as trabalhou_no_local_de_costume,
      C014 as contribui_inss,
      CAPITAL as capital,
      F002A2 as tem_alcool_no_domicilio,
      F002A3 as tem_mascara_no_domicilio,
      UF as unidade_federativa,
      V1013 as mes_da_pesquisa,
      V1022 as situacao_domicilio,
      V1023 as tipo_area

    FROM df_covid_com_valores
    '''
)


+-----+------+--------+-----+--------------------+------------------+-----+--------------------+------------+--------+--------------------+------+--------------+---------------+-----------------------+------------------+-------------+--------------------+---------------+-------------+----------------+------------+--------+---------+-------------+---------------------------+------------------+-----------------------------+---------------+----------+------------------+--------------------+--------------------------+------------------------------+-----------------------------+--------------+--------------------+-----------------------+------------------------+------------------+---------------+------------------+---------+
|idade|  sexo|cor_raca|febre|        escolaridade|perda_cheiro_sabor|tosse|dificuldade_respirar|foi_hospital|fez_swab|     resultado_teste|fadiga|plano_de_saude|fez_teste_covid|coleta_sangue_furo_dedo|coleta_sangue_veia|area_trabalho|         remuneracao|trabalho_remoto

In [0]:
covid_tratado = covid_tratado.where(col('mes_da_pesquisa') >= 9)

# Converte resultado para CSV

In [0]:
covid_tratado.write.mode('overwrite').option('header', 'true').csv(f'{GOLD_PATH}/covid_19_gold_csv')

# Converte resultado para Parquet

In [0]:
parquet_path = f'{GOLD_PATH}/covid_19_gold_parquet'
covid_parquet = covid_tratado.write.mode('overwrite').option('header', 'true').parquet(parquet_path)

In [0]:
display(covid_tratado)

idade sexo cor_raca febre escolaridade perda_cheiro_sabor tosse dificuldade_respirar foi_hospital fez_swab resultado_teste fadiga plano_de_saude fez_teste_covid coleta_sangue_furo_dedo coleta_sangue_veia area_trabalho remuneracao trabalho_remoto bolsa_familia frequenta_escola dor_muscular diarreia dor_peito ficou_em_casa tomou_remedio_conta_propria recebeu_visita_sus buscou_pronto_socorro_sus_upa ficou_internado foi_sedado tem_asma_bronquite cargo_no_trabalho qtd_empregados_no_trabalho remuneracao_em_todos_trabalhos trabalhou_no_local_de_costume contribui_inss capital tem_alcool_no_domicilio tem_mascara_no_domicilio unidade_federativa mes_da_pesquisa situacao_domicilio tipo_area 036 Homem Parda Não Médio completo Não Não Não null null Reduziu o contato com as pessoas, mas continuou saindo de casa para trabalho ou atividades não essenciais e/ou recebendo visitas Não Sim Não null null null Indica se o quesito foi respondido null Não null Não Não Não null null null null null null Não Outro técnico ou profissional de nível médio null Indica se o quesito foi respondido Sim null Município de Porto Velho (RO) Sim Sim Rondônia 09 Urbana Capital 030 Mulher Parda Não Superior completo Não Não Não null null Reduziu o contato com as pessoas, mas continuou saindo de casa para trabalho ou atividades não essenciais e/ou recebendo visitas Não Não Não null null null Indica se o quesito foi respondido null Não null Não Não Não null null null null null null Não Técnico, profissional da saúde de nível médio null Indica se o quesito foi respondido Sim Não Município de Porto Velho (RO) Sim Sim Rondônia 09 Urbana Capital 013 Homem Parda Não Fundamental incompleto Não Não Não null null Ficou rigorosamente em casa Não Sim Não null null null null null Não Sim Não Não Não null null null null null null Não null null null null null Município de Porto Velho (RO) Sim Sim Rondônia 09 Urbana Capital 011 Homem Parda Não Fundamental incompleto Não Não Não null null Ficou rigorosamente em casa Não Sim Não null null null null null Não Sim Não Não Não null null null null null null Não null null null null null Município de Porto Velho (RO) Sim Sim Rondônia 09 Urbana Capital 057 Mulher Branca Não Fundamental incompleto Não Não Não null null Reduziu o contato com as pessoas, mas continuou saindo de casa para trabalho ou atividades não essenciais e/ou recebendo visitas Não Não Não null null null null null Não null Não Não Não null null null null null null Não null null null null Não Município de Porto Velho (RO) Sim Sim Rondônia 09 Urbana Capital 058 Mulher Preta Não Sem instrução Não Não Não null null Ficou em casa e só saiu em caso de necessidade básica Não Não Não null null null Indica se o quesito foi respondido null Não null Não Não Não null null null null null null Não Outros null Indica se o quesito foi respondido Sim Não Município de Porto Velho (RO) Sim Sim Rondônia 09 Urbana Capital 047 Homem Parda Não Fundamental incompleto Não Não Não null null Reduziu o contato com as pessoas, mas continuou saindo de casa para trabalho ou atividades não essenciais e/ou recebendo visitas Não Não Não null null null Indica se o quesito foi respondido null Não null Não Não Não null null null null null null Não Pedreiro, servente de pedreiro, pintor, eletricista, marceneiro null Indica se o quesito foi respondido Sim Não Município de Porto Velho (RO) Sim Sim Rondônia 09 Urbana Capital 018 Mulher Parda Não Fundamental incompleto Não Não Não null null Ficou em casa e só saiu em caso de necessidade básica Não Não Não null null null null null Não Não Não Não Não null null null null null null Não null null null null Não Município de Porto Velho (RO) Sim Sim Rondônia 09 Urbana Capital 011 Homem Parda Não Fundamental incompleto Não Não Não null null Ficou rigorosamente em casa Não Não Não null null null null null Não Sim Não Não Não null null null null null null Não null null null null null Município de Porto Velho (RO) Sim Sim Rondônia 09 Urbana Capital 009 Mulher Parda Não Fundamen